In [1]:
import pandas as pd
from glob import glob

# Step 1: Load and Concatenate All Play-by-Play Files
pbp_files = sorted(glob("data/nba_playbyplay_*.csv"))

df_pbp_list = []
for file in pbp_files:
    print(f"Loading {file}")
    df = pd.read_csv(file)
    df_pbp_list.append(df)

pbp = pd.concat(df_pbp_list, ignore_index=True)
print(f"Total events across all seasons: {len(pbp):,}")


Loading data/nba_playbyplay_202021.csv
Loading data/nba_playbyplay_202122.csv
Loading data/nba_playbyplay_202223.csv
Loading data/nba_playbyplay_202324.csv
Loading data/nba_playbyplay_202425.csv
Total events across all seasons: 3,758,805


In [47]:
pd.set_option('display.float_format', '{:.0f}'.format)

pd.set_option('display.max_rows', None)

pd.set_option('display.max_columns', None)

In [30]:
pbp_all = pbp

In [31]:
# Load matchups
matchups = pd.read_csv("data/season_matchups.csv")

# Merge into play-by-play
pbp_all = pbp_all.merge(matchups[['GAME_ID', 'HOME_TEAM_ID', 'AWAY_TEAM_ID']], on='GAME_ID', how='left')


In [32]:
pbp_all = pbp_all.sort_values(["GAME_ID", "EVENTNUM"]).reset_index(drop=True)

# Split score string into away and home scores
score_split = pbp_all["SCORE"].str.split(" - ", expand=True)
pbp_all["AWAY_SCORE"] = pd.to_numeric(score_split[0], errors="coerce")
pbp_all["HOME_SCORE"] = pd.to_numeric(score_split[1], errors="coerce")

pbp_all[["HOME_SCORE", "AWAY_SCORE"]] = (
    pbp_all.groupby("GAME_ID")[["HOME_SCORE", "AWAY_SCORE"]].ffill()
)

pbp_all["HOME_SCORE"] = pbp_all["HOME_SCORE"].fillna(0).astype(int)
pbp_all["AWAY_SCORE"] = pbp_all["AWAY_SCORE"].fillna(0).astype(int)

In [60]:
# Subset of first 5 games
game_ids_to_test = [22000001, 22000002, 22000003, 22000004, 22000005]
pbp_subset = pbp_all[pbp_all["GAME_ID"].isin(game_ids_to_test)].copy()

# Optional: sort by GAME_ID and EVENTNUM for logical order
pbp_subset = pbp_subset.sort_values(["GAME_ID", "EVENTNUM"]).reset_index(drop=True)

# Preview the first few rows
pbp_subset

GAME_ID  EVENTNUM  EVENTMSGTYPE  EVENTMSGACTIONTYPE  PERIOD  \
0     22000001         2            12                   0       1   
1     22000001         4            10                   0       1   
2     22000001         7             5                  45       1   
3     22000001         8             6                   2       1   
4     22000001        10             3                  11       1   
5     22000001        11             3                  12       1   
6     22000001        12             1                  79       1   
7     22000001        13             1                 108       1   
8     22000001        16             1                  79       1   
9     22000001        18             2                   1       1   
10    22000001        19             4                   0       1   
11    22000001        20             1                  79       1   
12    22000001        21             2                  79       1   
13    22000001        22             4                   0       1   
14    22000001        23             1                   1       1   
15    22000001        25             2                   1       1   
16    22000001        26             4                   0       1   
17    22000001        27             2                   1       1   
18    22000001        28             4                   0       1   
19    22000001        29             1                  98       1   
20    22000001        31             2                   1       1   
21    22000001        32             4                   0       1   
22    22000001        33             2                   1       1   
23    22000001        34             4                   0       1   
24    22000001        35             2                  79       1   
25    22000001        36             4                   0       1   
26    22000001        37             2                  79       1   
27    22000001        38             4                   0       1   
28    22000001        39             1                  79       1   
29    22000001        40             6                   2       1   
30    22000001        42             3                  10       1   
31    22000001        43             6                   2       1   
32    22000001        45             3                  11       1   
33    22000001        46             3                  12       1   
34    22000001        47             2                  79       1   
35    22000001        48             4                   0       1   
36    22000001        50             2                   1       1   
37    22000001        51             4                   0       1   
38    22000001        52             1                   1       1   
39    22000001        54             6                   4       1   
40    22000001        56             5                  37       1   
41    22000001        57             2                  75       1   
42    22000001        58             4                   0       1   
43    22000001        59             2                   6       1   
44    22000001        60             4                   0       1   
45    22000001        63             1                   9       1   
46    22000001        65             9                   1       1   
47    22000001        66             8                   0       1   
48    22000001        68             2                   6       1   
49    22000001        70             4                   0       1   
50    22000001        71             1                  41       1   
51    22000001        72             2                  79       1   
52    22000001        73             4                   0       1   
53    22000001        74             6                   2       1   
54    22000001        76             3                  11       1   
55    22000001        77             4                   1       1   
56    22000001   

In [59]:
import math
import numpy as np

# Helper functions for event types

def is_made_shot(row):
    return row['EVENTMSGTYPE'] == 1

def is_turnover(row):
    return row['EVENTMSGTYPE'] == 5

def is_rebound(row):
    return row['EVENTMSGTYPE'] == 4

def is_offensive_rebound(row, last_possession_team):
    # Rebound by same team as possession team is offensive rebound
    return row['PLAYER1_TEAM_ID'] == last_possession_team

def is_defensive_rebound(row, last_possession_team):
    # Rebound by other team than possession team is defensive rebound
    return row['PLAYER1_TEAM_ID'] != last_possession_team

def is_end_of_period(row):
    # End of period or game: possession ends
    # Usually period 4 or OT periods and last event in period
    return row['PCTIMESTRING'] == '00:00'

def other_team(team_id, team1, team2):
    if team_id == team1:
        return team2
    elif team_id == team2:
        return team1
    else:
        # Defensive fallback: team_id doesn't match either; return None or raise error
        return None

    
def is_final_made_free_throw(row):
    """Returns True if the free throw is a final one and was made."""
    return (
        row['EVENTMSGTYPE'] == 3 and
        row['EVENTMSGACTIONTYPE'] in {10, 12, 15, 16, 19}
    )

def assign_possession_team(pbp):
    possession_team_list = []
    last_possession_team = None
    last_game_id = None
    last_period = None

    pbp = pbp.sort_values(['GAME_ID', 'PERIOD', 'EVENTNUM']).reset_index(drop=True)

    for i, row in pbp.iterrows():
        team1 = row['HOME_TEAM_ID']
        team2 = row['AWAY_TEAM_ID']

        current_game_id = row['GAME_ID']
        current_period = row['PERIOD']

        if (current_game_id != last_game_id) or (current_period != last_period):
            possession_team = row['HOME_TEAM_ID']
            last_possession_team = possession_team
            last_game_id = current_game_id
            last_period = current_period
            possession_team_list.append(possession_team)
            continue

        if is_made_shot(row):
            possession_team = other_team(last_possession_team, team1, team2)

        elif is_turnover(row):
            possession_team = other_team(last_possession_team, team1, team2)

        elif is_rebound(row):
            if is_offensive_rebound(row, last_possession_team):
                possession_team = last_possession_team
            else:
                possession_team = row['PLAYER1_TEAM_ID']

        elif is_final_made_free_throw(row):
            possession_team = other_team(last_possession_team, team1, team2)

        else:
            possession_team = last_possession_team

        possession_team_list.append(possession_team)
        last_possession_team = possession_team

    pbp['CURRENT_OFFENSIVE_TEAM_ID'] = possession_team_list
    return pbp
    
    
# Function to determine if an event ends a possession
def is_end_of_possession(i, row, pbp):
    if is_made_shot(row) or is_turnover(row) or is_end_of_period(row):
        return True
    
    if is_rebound(row):
        last_possession_team = pbp.loc[i-1, 'CURRENT_OFFENSIVE_TEAM_ID'] if i > 0 else None
        # Defensive rebound ends possession
        if row['PLAYER1_TEAM_ID'] != last_possession_team:
            return True
    
    return False


# Convert time string + period to seconds elapsed since game start
def time_to_seconds(time_str, period):
    minutes, seconds = map(int, time_str.split(':'))
    time_left_in_period = minutes * 60 + seconds
    period_elapsed = (period - 1) * 720  # 12 minutes per period
    return period_elapsed + (720 - time_left_in_period)


In [61]:
# 1. Assign possession team
pbp_subset = assign_possession_team(pbp_subset)

# 2. Assign possession IDs by iterating through pbp_all in order
possession_id = 0
last_game_id = None
possession_ids = []

pbp_subset = pbp_subset.sort_values(['GAME_ID', 'PERIOD', 'EVENTNUM']).reset_index(drop=True)

for i, row in pbp_subset.iterrows():
    current_game_id = row['GAME_ID']
    
    # Reset possession counter on new game
    if current_game_id != last_game_id:
        possession_id = 0
        last_game_id = current_game_id
    
    # Check if this event ends the possession
    if is_end_of_possession(i, row, pbp_subset):
        possession_id += 1
    
    possession_ids.append(possession_id)

pbp_subset['POSSESSION_ID'] = possession_ids

# 3. Calculate GAME_SECONDS for all rows
pbp_subset['GAME_SECONDS'] = pbp_subset.apply(
    lambda row: time_to_seconds(row['PCTIMESTRING'], row['PERIOD']), axis=1
)

# 4. Calculate SHOT_CLOCK by possession group (assuming 24s clock reset at possession start)
pbp_subset = pbp_subset.sort_values(['GAME_ID', 'POSSESSION_ID', 'GAME_SECONDS']).reset_index(drop=True)



In [62]:
def calculate_shot_clock(group):
    times = group['GAME_SECONDS']
    shot_clock = 24 - (times - times.min())
    #shot_clock = shot_clock.clip(lower=0)  # shot clock never < 0
    return shot_clock

pbp_subset['SHOT_CLOCK'] = pbp_subset.groupby(['GAME_ID', 'POSSESSION_ID']).apply(calculate_shot_clock).reset_index(level=[0,1], drop=True)


/var/folders/vc/57rv48yn701dfc_3bmv9xqwm0000gn/T/ipykernel_68861/3677648850.py:7: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  pbp_subset['SHOT_CLOCK'] = pbp_subset.groupby(['GAME_ID', 'POSSESSION_ID']).apply(calculate_shot_clock).reset_index(level=[0,1], drop=True)


In [63]:
pbp_subset[pbp_subset["GAME_ID"] == 22000004]

GAME_ID  EVENTNUM  EVENTMSGTYPE  EVENTMSGACTIONTYPE  PERIOD  \
1489  22000004         2            12                   0       1   
1490  22000004         4            10                   0       1   
1491  22000004         7             6                   2       1   
1492  22000004         9             3                  11       1   
1493  22000004        10             3                  12       1   
1494  22000004        11             2                   6       1   
1495  22000004        13             4                   0       1   
1496  22000004        14             2                  41       1   
1497  22000004        15             4                   0       1   
1498  22000004        16             2                   2       1   
1499  22000004        17             4                   0       1   
1500  22000004        18             1                   1       1   
1501  22000004        20             6                   1       1   
1502  22000004        22             6                   1       1   
1503  22000004        24             2                  80       1   
1504  22000004        25             4                   0       1   
1505  22000004        27             6                   4       1   
1506  22000004        29             5                  37       1   
1507  22000004        30             2                   6       1   
1508  22000004        32             4                   0       1   
1509  22000004        33             2                  72       1   
1510  22000004        34             4                   0       1   
1511  22000004        35             1                  41       1   
1512  22000004        36             2                   1       1   
1513  22000004        37             4                   0       1   
1514  22000004        38             2                   2       1   
1515  22000004        39             4                   0       1   
1516  22000004        40             1                  74       1   
1517  22000004        42             6                   2       1   
1518  22000004        44             3                  11       1   
1519  22000004        45             3                  12       1   
1520  22000004        46             1                   1       1   
1521  22000004        48             2                  47       1   
1522  22000004        49             4                   0       1   
1523  22000004        50             2                   2       1   
1524  22000004        51             4                   0       1   
1525  22000004        53             1                 103       1   
1526  22000004        54             2                   1       1   
1527  22000004        55             4                   0       1   
1528  22000004        56             6                   4       1   
1529  22000004        61             2                  97       1   
1530  22000004        62             4                   0       1   
1531  22000004        58             5                  37       1   
1532  22000004        59             8                   0       1   
1533  22000004        63             1                   6       1   
1534  22000004        65             6                   1       1   
1535  22000004        67             2                   1       1   
1536  22000004        68             4                   0       1   
1537  22000004        69             2                   3       1   
1538  22000004        70             4                   0       1   
1539  22000004        71             2                  79       1   
1540  22000004        72             4                   0       1   
1541  22000004        73             6                   2       1   
1542  22000004        75             3                  11       1   
1543  22000004        76             3                  12       1   
1544  22000004        77             5                  40       1   
1545  22000004   

In [23]:
pbp_subset.to_csv("pbp_subset.csv", index=False)

In [ ]:


def calculate_shot_clock(group):
    times = group['GAME_SECONDS']
    shot_clock = 24 - (times - times.min())
    shot_clock = shot_clock.clip(lower=0)  # shot clock never < 0
    return shot_clock

pbp_all['SHOT_CLOCK'] = pbp_all.groupby(['GAME_ID', 'POSSESSION_ID']).apply(calculate_shot_clock).reset_index(level=[0,1], drop=True)

# Done! Now pbp_all has:
# - CURRENT_OFFENSIVE_TEAM_ID (possession team at each event)
# - POSSESSION_ID (unique possession identifier)
# - GAME_SECONDS (seconds elapsed in game)
# - SHOT_CLOCK (estimated shot clock time remaining)


In [26]:
import numpy as np



    # Home shot → margin is fine as-is
    # Away shot → flip the sign
    return margin if is_home else -margin

# Make sure SCOREMARGIN is numeric
merged_df['SCOREMARGIN'] = pd.to_numeric(merged_df['SCOREMARGIN'], errors='coerce')
merged_df['SCOREMARGIN_NORMALIZED'] = merged_df.apply(normalize_margin, axis=1)


In [ ]:
def normalize_score_margin(row):
    margin = row['SCOREMARGIN']
    if pd.isna(margin) or margin == "TIE":
        return 0

    try:
        margin_val = int(margin)
    except:
        return np.nan

    # Flip if shooter is away team
    if row['TEAM_ID'] != row['HOME_TEAM_ID']:
        return -margin_val
    else:
        return margin_val

merged_df['SCOREMARGIN_NORMALIZED'] = merged_df.apply(normalize_score_margin, axis=1)


# Fill missing margin values forward first (still sorted by game and event)
merged_df['PRE_EVENT_MARGIN'] = (
    merged_df
    .groupby('GAME_ID')['SCOREMARGIN_NORMALIZED']
    .ffill()
)

# Now shift it by one *within each game* to get the pre-shot margin
merged_df['PRE_SHOT_MARGIN'] = (
    merged_df
    .groupby('GAME_ID')['PRE_EVENT_MARGIN']
    .shift(1)
)

merged_df['PRE_SHOT_MARGIN'].fillna(0, inplace=True)

def bucket_score_margin(margin):
    if pd.isna(margin):
        return "Unknown"
    margin = int(margin)
    if margin <= -15:
        return "<= -15"
    elif margin <= -10:
        return "-15 to -10"
    elif margin <= -5:
        return "-10 to -5"
    elif margin <= -3:
        return "-5 to -3"
    elif -2 <= margin <= 2:
        return "Within ±2"
    elif margin <= 5:
        return "3 to 5"
    elif margin <= 10:
        return "5 to 10"
    elif margin <= 15:
        return "10 to 15"
    else:
        return "> 15"

merged_df['SCOREMARGIN_BUCKET'] = merged_df['PRE_SHOT_MARGIN'].apply(bucket_score_margin)


In [13]:
merged_df.sort_values(['GAME_ID','EVENTNUM']).head(50)

GRID_TYPE   GAME_ID  EVENTNUM  PLAYER_ID        PLAYER_NAME     TEAM_ID              TEAM_NAME  PERIOD_SHOT  MINUTES_REMAINING  SECONDS_REMAINING   EVENT_TYPE                      ACTION_TYPE       SHOT_TYPE        SHOT_ZONE_BASIC         SHOT_ZONE_AREA  SHOT_ZONE_RANGE  SHOT_DISTANCE  LOC_X  LOC_Y  SHOT_ATTEMPTED_FLAG  SHOT_MADE_FLAG  GAME_DATE  HTM  VTM SEASON_SHOT  EVENTMSGTYPE  EVENTMSGACTIONTYPE  PERIOD_PBP WCTIMESTRING PCTIMESTRING                                         HOMEDESCRIPTION NEUTRALDESCRIPTION                                     VISITORDESCRIPTION    SCORE SCOREMARGIN  PERSON1TYPE  PLAYER1_ID       PLAYER1_NAME  PLAYER1_TEAM_ID PLAYER1_TEAM_CITY PLAYER1_TEAM_NICKNAME PLAYER1_TEAM_ABBREVIATION  PERSON2TYPE  PLAYER2_ID       PLAYER2_NAME  PLAYER2_TEAM_ID PLAYER2_TEAM_CITY PLAYER2_TEAM_NICKNAME PLAYER2_TEAM_ABBREVIATION  PERSON3TYPE  PLAYER3_ID    PLAYER3_NAME  PLAYER3_TEAM_ID PLAYER3_TEAM_CITY PLAYER3_TEAM_NICKNAME PLAYER3_TEAM_ABBREVIATION  VIDEO_AVAILABLE_FLAG SEASON_PBP
118813  Shot Chart Detail  22000001        12     202681       Kyrie Irving  1610612751          Brooklyn Nets            1                 11                 22    Made Shot                 Pullup Jump shot  2PT Field Goal              Mid-Range              Center(C)        16-24 ft.             22     -2    220                    1               1   20201222  BKN  GSW      202021           1.0                79.0         1.0      7:08 PM        11:22      Irving 22' Pullup Jump Shot (2 PTS) (Durant 1 AST)                NaN                                                    NaN    2 - 2         TIE          4.0    202681.0       Kyrie Irving     1.610613e+09          Brooklyn                  Nets                       BKN          4.0    201142.0       Kevin Durant     1.610613e+09          Brooklyn                  Nets                       BKN          0.0         0.0             NaN              NaN               NaN                   NaN                       NaN                   1.0     202021
83605   Shot Chart Detail  22000001        13    1630164      James Wiseman  1610612744  Golden State Warriors            1                 11                 11    Made Shot                Cutting Dunk Shot  2PT Field Goal        Restricted Area              Center(C)  Less Than 8 ft.              0      9     -2                    1               1   20201222  BKN  GSW      202021           1.0               108.0         1.0      7:08 PM        11:11                                                     NaN                NaN   Wiseman 1' Cutting Dunk Shot (2 PTS) (Wiggins 1 AST)    4 - 2          -2          5.0   1630164.0      James Wiseman     1.610613e+09      Golden State              Warriors                       GSW          5.0    203952.0     Andrew Wiggins     1.610613e+09      Golden State              Warriors                       GSW          0.0         0.0             NaN              NaN               NaN                   NaN                       NaN                   1.0     202021
111598  Shot Chart Detail  22000001        16     201142       Kevin Durant  1610612751          Brooklyn Nets            1                 10                 49    Made Shot                 Pullup Jump shot  3PT Field Goal      Above the Break 3              Center(C)          24+ ft.             25    -20    258                    1               1   20201222  BKN  GSW      202021           1.0                79.0         1.0      7:09 PM        10:49  Durant 26' 3PT Pullup Jump Shot (3 PTS) (Harris 1 AST)                NaN                                                    NaN    4 - 5           1          4.0    201142.0       Kevin Durant     1.610613e+09          Brooklyn                  Nets                       BKN          4.0    203925.0         Joe Harris     1.610613e+09          Brooklyn                  Nets                       BKN          0.0         0.0             NaN              NaN               NaN                  